In [1]:
import pandas as pd
import torch
from torch import nn
import aditmaz95

In [2]:
data=aditmaz95.KaggleHouse(batch_size=64)
print(data.raw_train.shape)
print(data.raw_val.shape)

(1460, 81)
(1459, 80)


In [3]:
print(data.raw_train.iloc[:4, [0, 1, 2, 3, -3, -2, -1]])

   Id  MSSubClass MSZoning  LotFrontage SaleType SaleCondition  SalePrice
0   1          60       RL         65.0       WD        Normal     208500
1   2          20       RL         80.0       WD        Normal     181500
2   3          60       RL         68.0       WD        Normal     223500
3   4          70       RL         60.0       WD       Abnorml     140000


In [4]:
data.preprocess()
data.train.shape

(1460, 331)

In [5]:
trainer = aditmaz95.Trainer(max_epochs=200)
models = aditmaz95.k_fold(trainer, data, k=5, lr=0.01)

average validation log mse = 0.033093972578644756


In [6]:
preds = [model(torch.tensor(data.val.values.astype(float), dtype=torch.float32))
         for model in models]
# Taking exponentiation of predictions in the logarithm scale
ensemble_preds = torch.exp(torch.cat(preds, 1)).mean(1)
submission = pd.DataFrame({'Id':data.raw_val.Id,
                           'SalePrice':ensemble_preds.detach().numpy()})
submission.to_csv('kaggle_house_prices/submission.csv', index=False)